In [1]:
from utils import *         # 데이터 전처리 함수 및 활용 함수      
from model import *

In [2]:
# 데이터 전처리 완료
df,Category_variables,Numeric_variables,Target_variables = data_processing()

In [ ]:
from sklearn.model_selection import train_test_split

# 공통 테스트셋
df_all = df.copy()
train_val_df, test_df = train_test_split(df_all, test_size=0.2, random_state=42, stratify=None)  

In [6]:
# 전체 모델 학습 : 오래 걸림.
model_all = get_model(model_name='random_forest', max_depth=10, random_state=0)
X_train_all = train_val_df[list(Category_variables)+Numeric_variables]
y_train_all = train_val_df[Target_variables]
model_all.fit(X_train_all, y_train_all)

X_test = test_df[list(Category_variables)+Numeric_variables]
y_test = test_df[Target_variables]

y_pred_all = model_all.predict(X_test)


c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)


In [7]:
# 구간별 모델 학습

temperature_bins = {
    'cat1': train_val_df[train_val_df['Temperature'] < 1100],
    'cat2': train_val_df[(train_val_df['Temperature'] >= 1100) & (train_val_df['Temperature'] < 1120)],
    'cat3': train_val_df[(train_val_df['Temperature'] >= 1120) & (train_val_df['Temperature'] < 1140)],
    'cat4': train_val_df[(train_val_df['Temperature'] >= 1140) & (train_val_df['Temperature'] < 1160)],
    'cat5': train_val_df[train_val_df['Temperature'] >= 1160]
}

models_by_bin = {}

for name, subset in temperature_bins.items():
    X_train = subset[list(Category_variables)+Numeric_variables]
    y_train = subset[Target_variables]
    model = get_model(model_name='random_forest', max_depth=10, random_state=0)
    model.fit(X_train, y_train)
    models_by_bin[name] = model


c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\base.py:1389: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\base.py:1389: DataConversionWarning: A column-vector y was passed whe

In [8]:
# 구간별 모델로 테스트셋 예측
def get_bin(temp):
    if temp < 1100: return 'cat1'
    elif temp < 1120: return 'cat2'
    elif temp < 1140: return 'cat3'
    elif temp < 1160: return 'cat4'
    else: return 'cat5'

y_pred_bin = []

for idx, row in test_df.iterrows():
    bin_name = get_bin(row['Temperature'])
    model = models_by_bin[bin_name]
    x_input = row[list(Category_variables)+Numeric_variables].values.reshape(1, -1)
    y_pred_bin.append(model.predict(x_input)[0])

y_pred_bin = np.array(y_pred_bin)


c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have valid feature names, but RandomForestRegressor was fitted with feature names
  warnings.warn(
c:\Users\DANIK\anaconda3\envs\diwork_latest\lib\site-packages\sklearn\utils\validation.py:2739: UserWarning: X does not have

In [9]:
from sklearn.metrics import mean_squared_error, r2_score

print("=== 전체 모델 ===")
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred_all)))
print("R2:", r2_score(y_test, y_pred_all))

print("=== 구간별 모델 ===")
print("RMSE:", np.sqrt(mean_squared_error(y_test, y_pred_bin)))
print("R2:", r2_score(y_test, y_pred_bin))


=== 전체 모델 ===
RMSE: 23.239226195999507
R2: 0.9536063043348959
=== 구간별 모델 ===
RMSE: 20.653847194932876
R2: 0.9633547606819903
